In [15]:
import pandas as pd
prices = pd.read_csv("all_stocks.csv")
prices.rename(columns={"Date":"ds", "Ticker":"unique_id", "Close":"y"}, inplace=True)
prices["ds"] = prices["ds"].str[:10] # remove time
prices["ds"] = pd.to_datetime(prices["ds"])
prices = prices[["ds", "y", "unique_id","12-day EMA", "26-day EMA", "MACD", "Signal Line", "MACD Histogram", "RSI", "OBV"]]
prices.dropna(inplace=True)

In [17]:
# Train / Test split
train_size = 0.8  # 80% train, 20% test
def train_test_split(group):
    split_index = int(len(group) * train_size)
    return group.iloc[:split_index], group.iloc[split_index:]

# Apply the split to each unique stock (grouped by 'unique_id')
train_data, test_data = zip(*prices.groupby("unique_id").apply(train_test_split))

# Convert tuple results to DataFrames
df_train = pd.concat(train_data).reset_index(drop=True)
df_test = pd.concat(test_data).reset_index(drop=True)

/var/folders/vw/fk4p6s510g7dfnhknk592c7r0000gn/T/ipykernel_85207/359759405.py:8: DeprecationWarning: DataFrameGroupBy.apply operated on the grouping columns. This behavior is deprecated, and in a future version of pandas the grouping columns will be excluded from the operation. Either pass `include_groups=False` to exclude the groupings or explicitly select the grouping columns after groupby to silence this warning.
  train_data, test_data = zip(*prices.groupby("unique_id").apply(train_test_split))


In [18]:
from neuralforecast import NeuralForecast
from neuralforecast.models import TimeLLM

input_sizes = [10,15,30,60,90] #historical window
#input_sizes = [10] #historical window

prompt_prefix = "The dataset contains closing stock prices and its supporting technical indicators: MACD, OBV, RSI."

for interval in input_sizes:
    timellm = TimeLLM(h=100,
                    input_size=interval,
                    prompt_prefix=prompt_prefix,
                    batch_size=16,
                    valid_batch_size=16,
                    max_steps=50,
                    windows_batch_size=16)

    nf = NeuralForecast(
        models=[timellm],
        freq='D'
    )
    print(f"Training for interval: {interval}")
    nf.fit(df=df_train)
    
    #test_df_future = nf.make_future_dataframe(df_train)
    forecasts = nf.predict(df_train)
    print(f"Reults for interval: {interval}")
    print(forecasts)
    test_results = pd.merge(df_test, forecasts, on=["ds", "unique_id"], how="inner") #LSTM (=predicted), y (=actual)
    test_results.to_csv(f"res_llmtime_{interval}.csv")


Seed set to 1


Using openai-community/gpt2 as default.
Successfully loaded model: openai-community/gpt2


/usr/local/anaconda3/envs/neuralforecast12/lib/python3.12/site-packages/neuralforecast/common/_base_model.py:349: UserWarning: val_check_steps is greater than max_steps, setting val_check_steps to max_steps.
  warnings.warn(
GPU available: False, used: False
TPU available: False, using: 0 TPU cores
HPU available: False, using: 0 HPUs

  | Name                | Type               | Params | Mode 
-------------------------------------------------------------------
0 | loss                | MAE                | 0      | train
1 | padder_train        | ConstantPad1d      | 0      | train
2 | scaler              | TemporalNorm       | 0      | train
3 | llm                 | GPT2Model          | 124 M  | eval 
4 | patch_embedding     | PatchEmbedding     | 1.5 K  | train
5 | mapping_layer       | Linear             | 51.5 M | train
6 | reprogramming_layer | ReprogrammingLayer | 2.4 M  | train
7 | output_projection   | FlattenHead        | 12.9 K | train
8 | normalize_layers    | RevIN      

Training for interval: 10


Sanity Checking: |          | 0/? [00:00<?, ?it/s]

...

Training: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

`Trainer.fit` stopped: `max_steps=50` reached.
GPU available: False, used: False
TPU available: False, using: 0 TPU cores
HPU available: False, using: 0 HPUs


Predicting: |          | 0/? [00:00<?, ?it/s]

Reults for interval: 90
    unique_id         ds     TimeLLM
0        AAPL 2023-02-18  146.046051
1        AAPL 2023-02-19  141.594269
2        AAPL 2023-02-20  143.290802
3        AAPL 2023-02-21  146.852692
4        AAPL 2023-02-22  144.115921
..        ...        ...         ...
495      TSLA 2023-05-24  139.532669
496      TSLA 2023-05-25  203.212784
497      TSLA 2023-05-26  170.545776
498      TSLA 2023-05-27  215.745560
499      TSLA 2023-05-28  196.658554

[500 rows x 3 columns]


In [2]:
import numpy as np
import pandas as pd

input_sizes = [10,15,30,60,90]

# Define function for MAE calculation
def calculate_mae(y_true, y_pred):
    return np.mean(np.abs(np.array(y_true) - np.array(y_pred)))

# Define function for RMSE calculation
def calculate_rmse(y_true, y_pred):
    return np.sqrt(np.mean((np.array(y_true) - np.array(y_pred)) ** 2))

# Define function for RMAE calculation
def calculate_rmae(mae, avg_price):
    return (mae / avg_price) * 100 if avg_price != 0 else np.nan

# List to store per-stock results
detailed_results = []

# Iterate over each interval
for interval in input_sizes:
    df = pd.read_csv(f"TIMELLM_RESULTS_PER_STOCK/res_llmtime_{interval}.csv")

    # Calculate RMSE, MAE, and RMAE for each unique_id (each stock separately)
    grouped_results = df.groupby("unique_id").apply(lambda group: {
        "unique_id": group["unique_id"].iloc[0],
        "Interval": interval,
        "MAE": calculate_mae(group["y"], group["TimeLLM"]),
        "RMSE": calculate_rmse(group["y"], group["TimeLLM"]),
        "RMAE": calculate_rmae(
            calculate_mae(group["y"], group["TimeLLM"]),
            np.mean(group["y"])  # Average price in the interval
        )
    }).tolist()  # Convert to list of dicts

    # Append per-stock results
    detailed_results.extend(grouped_results)

# Save results as DataFrame
detailed_results_df = pd.DataFrame(detailed_results)
detailed_results_df.to_csv("results_timellm.csv", index=False)


/var/folders/vw/fk4p6s510g7dfnhknk592c7r0000gn/T/ipykernel_69055/3030272374.py:26: DeprecationWarning: DataFrameGroupBy.apply operated on the grouping columns. This behavior is deprecated, and in a future version of pandas the grouping columns will be excluded from the operation. Either pass `include_groups=False` to exclude the groupings or explicitly select the grouping columns after groupby to silence this warning.
  grouped_results = df.groupby("unique_id").apply(lambda group: {
/var/folders/vw/fk4p6s510g7dfnhknk592c7r0000gn/T/ipykernel_69055/3030272374.py:26: DeprecationWarning: DataFrameGroupBy.apply operated on the grouping columns. This behavior is deprecated, and in a future version of pandas the grouping columns will be excluded from the operation. Either pass `include_groups=False` to exclude the groupings or explicitly select the grouping columns after groupby to silence this warning.
  grouped_results = df.groupby("unique_id").apply(lambda group: {
/var/folders/vw/fk4p6s51